# Mutiple classification

The objective of this exercise is to find the best model capable of predicting the correct class among 11 possibilities, from 64 binary variables.

Predictions will be evaluated based on MPA@3 (Mean Average Precision at 3)
Each model can predict up to 3 predictions, and the earlier a correct prediction occurs, the higher score it will receive.


# Get the data

In [1]:
import pandas as pd
df = pd.read_csv('train.csv')
df.head()

id  sudden_fever  headache  mouth_bleed  nose_bleed  muscle_pain  \
0   0           1.0       1.0          0.0         1.0          1.0   
1   1           0.0       0.0          0.0         0.0          0.0   
2   2           0.0       1.0          1.0         1.0          0.0   
3   3           0.0       0.0          1.0         1.0          1.0   
4   4           0.0       0.0          0.0         0.0          0.0   

   joint_pain  vomiting  rash  diarrhea  ...  breathing_restriction  \
0         1.0       1.0   0.0       1.0  ...                    0.0   
1         0.0       1.0   0.0       1.0  ...                    0.0   
2         1.0       1.0   1.0       1.0  ...                    1.0   
3         1.0       0.0   1.0       0.0  ...                    0.0   
4         0.0       0.0   0.0       1.0  ...                    0.0   

   toe_inflammation  finger_inflammation  lips_irritation  itchiness  ulcers  \
0               0.0                  0.0              0.0        0.0     0.0   
1               0.0                  0.0              0.0        0.0     0.0   
2               1.0                  1.0              1.0        1.0     0.0   
3               0.0                  0.0              0.0        0.0     0.0   
4               1.0                  0.0              0.0        1.0     1.0   

   toenail_loss  speech_problem  bullseye_rash          prognosis  
0           0.0             0.0            0.0       Lyme_disease  
1           0.0             0.0            0.0          Tungiasis  
2           1.0             1.0            1.0       Lyme_disease  
3           0.0             0.0            0.0               Zika  
4           1.0             0.0            0.0  Rift_Valley_fever  

[5 rows x 66 columns]

In [2]:
df=df.drop('id',axis=1)
df['prognosis'].value_counts()

West_Nile_fever          85
Japanese_encephalitis    81
Tungiasis                70
Rift_Valley_fever        70
Chikungunya              66
Dengue                   63
Yellow_Fever             61
Zika                     58
Plague                   53
Lyme_disease             52
Malaria                  48
Name: prognosis, dtype: int64

In [3]:
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split

label_encoder = LabelEncoder()

# Encode the "prognosis" column
df['prognosis'] = label_encoder.fit_transform(df['prognosis'])

# We split out our own test set
X_train, X_test, y_train, y_test = train_test_split(df.drop('prognosis', axis=1), df['prognosis'], random_state=42)

# ATTENTION : ici il faut remplacer xxxxx et XXXXX par le modèle de votre choix...

In [4]:
# choose the model XXXXX from sklearn
from sklearn.xxxxx import XXXXX

# We'll train a simple XXXXX model on our training split
lr_clf = XXXXX()
lr_clf.fit(X_train, y_train)

# Normally lr_clf.predict would just predict the most likely prognosis, but with predict_proba we can get probabilities for all possible prognoses.
predictions = lr_clf.predict_proba(X_test)

ModuleNotFoundError: ignored

In [ ]:
# Lets take a look at getting our top 3 prognoses for just a single prediction first
print("Output of predict_proba:")
print(predictions[0])

# We can get the indices of the highest probabilities with argsort
sorted_prediction_ids = np.argsort(-predictions[0]) # Note argsort sorts in ascending order, but by making all our values negative we'll end up with the highest probabilities first
print("Indices sorted by probabilities:")
print(sorted_prediction_ids)
# 2 is our first id, and the probability at index 2 from predictions[0] is the highest

In [ ]:
# We can grab the top 3 predictions and then use our encoder to turn them back into string labels
top_3_prediction_ids = sorted_prediction_ids[:3]
top_3_predictions = label_encoder.inverse_transform(top_3_prediction_ids.reshape(-1, 1)) # inverse_transform expects a 2D array, so we reshape our vector (but this won't be necessary when we run on multiple predictions at once)
top_3_predictions
# We got a list of 3 predictions! Great!

In [ ]:
# Now let's look at doing the above for a whole set of predictions at once:
sorted_prediction_ids = np.argsort(-predictions, axis=1)
top_3_prediction_ids = sorted_prediction_ids[:,:3]

# Because enc.inverse_transform expects a specific shape (a 2D array with 1 column) we can save the original shape to reshape to after decoding
original_shape = top_3_prediction_ids.shape
top_3_predictions = label_encoder.inverse_transform(top_3_prediction_ids.reshape(-1, 1))
top_3_predictions = top_3_predictions.reshape(original_shape)
top_3_predictions[:10] # Spot check our first 10 values

In [ ]:
import numpy as np

def apk(actual, predicted, k=10):
    """
    Computes the average precision at k.
    This function computes the average prescision at k between two lists of
    items.
    Parameters
    ----------
    actual : list
             A list of elements that are to be predicted (order doesn't matter)
    predicted : list
                A list of predicted elements (order does matter)
    k : int, optional
        The maximum number of predicted elements
    Returns
    -------
    score : double
            The average precision at k over the input lists
    """
    if not actual:
        return 0.0

    if len(predicted)>k:
        predicted = predicted[:k]

    score = 0.0
    num_hits = 0.0

    for i,p in enumerate(predicted):
        # first condition checks whether it is valid prediction
        # second condition checks if prediction is not repeated
        if p in actual and p not in predicted[:i]:
            num_hits += 1.0
            score += num_hits / (i+1.0)

    return score / min(len(actual), k)

def mapk(actual, predicted, k=10):
    """
    Computes the mean average precision at k.
    This function computes the mean average prescision at k between two lists
    of lists of items.
    Parameters
    ----------
    actual : list
             A list of lists of elements that are to be predicted
             (order doesn't matter in the lists)
    predicted : list
                A list of lists of predicted elements
                (order matters in the lists)
    k : int, optional
        The maximum number of predicted elements
    Returns
    -------
    score : double
            The mean average precision at k over the input lists
    """
    return np.mean([apk(a,p,k) for a,p in zip(actual, predicted)])

In [ ]:
# Models are evaluated based on MPA@3
mapk(y_test.values.reshape(-1, 1), top_3_prediction_ids, k=3)